In [ ]:
# THIS SCRIPT WAS USED IN ORDER TO:

# CALCULATE THE RSA FOR EACH RESIDUE OF THE AB::AG COMPLEXES TO BE DOCKED, IN ORDER TO ELIMINATE THE PREDICTED PARATOPE RESIDUES (proABC-2) TO BE REMOVED
# CALCULATE THE RSA FOR ALL THE OVER 2000 AB::AG COMPLEXES, IN ORDER TO INVESTIGATE INTERFACE PROPENSITY, NON-INTERACTING SURFACES PROPENSITY AND CORE PROPENSITY

In [26]:
# Importing libraries
import freesasa
import pandas as pd
import math
from pathlib import Path

In [28]:
# Defining the directories with the PDB file collection, and where to save the output .csv files
#pdb_folder = Path('/Users/lorenzosisti/Downloads/SASA_for_docking/')
#output_folder = Path('/Users/lorenzosisti/Downloads/SASA_for_docking/')

pdb_folder = Path('/Users/lorenzosisti/Downloads/database_settembre_renamed/')
output_folder = Path('/Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/')

In [29]:
# Creating a dictionary containing the 20 experimentally derived maximum allowed solvent accessibility values reported in Tien et al. (2023).
max_acc = {
    'ALA': 121.0,
    'ARG': 265.0,
    'ASN': 187.0,
    'ASP': 187.0,
    'CYS': 148.0,
    'GLN': 214.0,
    'GLU': 214.0,
    'GLY': 97.0,
    'HIS': 216.0,
    'ILE': 195.0,
    'LEU': 191.0,
    'LYS': 230.0,
    'MET': 203.0,
    'PHE': 228.0,
    'PRO': 154.0,
    'SER': 143.0,
    'THR': 163.0,
    'TRP': 264.0,
    'TYR': 255.0,
    'VAL': 165.0
}

In [30]:
# Defining a function to compute the relative solvent accessibility (RSA) of each residue
def compute_rsa(row, max_acc_dict):
    """
    Calcola la Relative Solvent Accessibility (RSA) per un residuo.

    Parametri:
    ----------
    row : pandas.Series
        Riga di un DataFrame contenente almeno le colonne 'ResName' e 'SASA'.
    max_acc_dict : dict
        Dizionario con i valori massimi di solvent accessibility per ciascun amminoacido.

    Ritorna:
    --------
    float
        Valore RSA = SASA / valore massimo teorico.
        Restituisce NaN se il residuo non è standard o il valore massimo è mancante.
    """
    aa = row["ResName"]
    sasa = row["SASA"]

    if aa in max_acc_dict and sasa is not None:
        maxval = max_acc_dict[aa]
        # evita divisione per zero
        if maxval and not math.isclose(maxval, 0.0):
            return sasa / maxval

    return float("nan")


In [32]:
# Function to process each PDB file (i.e. computing SASA and RSA)
def process_pdb(pdb_path, max_acc_dict):
    """
    Calcola la SASA e la RSA per tutti i residui in una struttura PDB.

    Parametri:
    ----------
    pdb_path : Path o str
        Percorso del file PDB da analizzare.
    max_acc_dict : dict
        Dizionario con i valori massimi di solvent accessibility per ciascun amminoacido.

    Ritorna:
    --------
    pandas.DataFrame
        DataFrame con colonne: ['Chain', 'ResNum', 'ResName', 'SASA', 'RSA', 'PDB']
    """
    # Legge la struttura e calcola la SASA con freesasa
    structure = freesasa.Structure(str(pdb_path))
    result = freesasa.calc(structure)

    # --- Estrai SASA per ogni atomo ---
    records = []
    for i in range(structure.nAtoms()):
        chain = structure.chainLabel(i)
        resnum = structure.residueNumber(i)
        resname = structure.residueName(i).upper()
        sasa_atom = result.atomArea(i)
        records.append([chain, resnum, resname, sasa_atom])

    # --- Crea DataFrame e somma SASA per residuo ---
    df_atoms = pd.DataFrame(records, columns=["Chain", "ResNum", "ResName", "AtomSASA"])
    df_res = df_atoms.groupby(["Chain", "ResNum", "ResName"], as_index=False)["AtomSASA"].sum()
    df_res = df_res.rename(columns={"AtomSASA": "SASA"})

    # --- Calcola RSA per ciascun residuo usando la funzione compute_rsa ---
    df_res["RSA"] = df_res.apply(lambda row: compute_rsa(row, max_acc_dict), axis=1)

    # --- Aggiunge nome del file PDB per tracciabilità ---
    df_res["PDB"] = Path(pdb_path).name

    # Arrotonda i valori per leggibilità
    #df_res["SASA"] = df_res["SASA"].round(3)
    #df_res["RSA"] = df_res["RSA"].round(4)

    return df_res


In [9]:
# Trying the workflow on a single PDB file
#df_example = process_pdb("/Users/lorenzosisti/Downloads/9cci_chothia.pdb", max_acc)
#df_example.head()

Chain ResNum ResName     SASA     RSA               PDB
0     A   319      ARG  262.167  0.9893  9cci_chothia.pdb
1     A   320      VAL  139.347  0.8445  9cci_chothia.pdb
2     A   321      GLN  133.295  0.6229  9cci_chothia.pdb
3     A   322      PRO  117.059  0.7601  9cci_chothia.pdb
4     A   323      THR  141.126  0.8658  9cci_chothia.pdb

In [33]:
# Batch run on all the PDB in the folder of interest
pdb_files = sorted([p for p in pdb_folder.iterdir() if p.suffix.lower() in (".pdb", ".ent")])
if not pdb_files:
    raise FileNotFoundError(f"Nessun file .pdb trovato in {pdb_folder}")

combined_list = []
failed = []
combined_csv = output_folder / "combined_sasa_rsa.csv"

for pdb in pdb_files:
    try:
        print(f"Processing {pdb.name} ...")
        df_res = process_pdb(pdb, max_acc)
        # salva csv per singola struttura
        out_csv = output_folder / f"{pdb.stem}_sasa_rsa.csv"
        df_res.to_csv(out_csv, index=False)
        print(f"  → salvato: {out_csv}")
        combined_list.append(df_res)
    except Exception as e:
        print(f"  ! Errore su {pdb.name}: {e}")
        failed.append((pdb.name, str(e)))
        # continua con i file successivi

# salva file combinato
if combined_list:
    combined_df = pd.concat(combined_list, ignore_index=True)
    combined_df.to_csv(combined_csv, index=False)
    print(f"\n✅ File combinato salvato: {combined_csv} (righe: {len(combined_df)})")
else:
    print("\n⚠️ Nessun file processato correttamente, nessun file combinato creato.")

if failed:
    print("\nAlcuni file non sono stati processati:")
    for name, err in failed:
        print(" -", name, ":", err)
else:
    print("\nTutti i file processati con successo.")

Processing 1a3r.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1a3r_sasa_rsa.csv
Processing 1acy.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1acy_sasa_rsa.csv
Processing 1adq.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1adq_sasa_rsa.csv
Processing 1afv.pdb ...


FreeSASA: warning: atom 'GLU  OT1' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'GLU  OT2' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'SER  OT1' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'SER  OT2' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: at

  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1afv_sasa_rsa.csv
Processing 1ahw.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1ahw_sasa_rsa.csv
Processing 1bgx.pdb ...


FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'GLY  OT1' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'GLY  OT2' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: at

  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1bgx_sasa_rsa.csv
Processing 1bj1.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1bj1_sasa_rsa.csv
Processing 1bvk.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1bvk_sasa_rsa.csv
Processing 1cfs.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1cfs_sasa_rsa.csv
Processing 1dee.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1dee_sasa_rsa.csv
Processing 1e4x.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/1e4x_sasa_rsa.csv
Processing 1e6j.pdb ...


...

  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/9qbj_sasa_rsa.csv
Processing 9qqn.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/9qqn_sasa_rsa.csv
Processing 9quw.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/9quw_sasa_rsa.csv
Processing 9r2e.pdb ...


FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ASN  OT1' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'ASN  OT2' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: at

  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/9r2e_sasa_rsa.csv
Processing 9rm2.pdb ...
  → salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/9rm2_sasa_rsa.csv


FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: atom 'TYR  OT1' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'TYR  OT2' unknown, guessing element is ' O', and radius 1.520 A
FreeSASA: warning: atom 'ILE  CD ' unknown, guessing element is ' C', and radius 1.700 A
FreeSASA: warning: at


✅ File combinato salvato: /Users/lorenzosisti/Downloads/SASA_for_ab_ag_int_characterization/combined_sasa_rsa.csv (righe: 1018737)

Tutti i file processati con successo.


In [2]:
structure = freesasa.Structure("/Users/lorenzosisti/Downloads/9cci_chothia.pdb")
result = freesasa.calc(structure)
areas = freesasa.classifyResults(result, structure)

In [3]:
# Estrai SASA per residuo
records = []
for i in range(structure.nAtoms()):
    atom = structure.atomName(i)
    resi = structure.residueName(i)
    resnum = structure.residueNumber(i)
    chain = structure.chainLabel(i)
    sasa = result.atomArea(i)
    records.append([chain, resnum, resi, sasa])

# Crea DataFrame
df = pd.DataFrame(records, columns=["Chain", "ResNum", "ResName", "SASA"])

# Raggruppa per residuo (somma gli atomi)
df_res = df.groupby(["Chain", "ResNum", "ResName"], as_index=False)["SASA"].sum()

# Salva in CSV
df_res.to_csv("/Users/lorenzosisti/Downloads/sasa_residues.csv", index=False)

print("✅ File 'sasa_residues.csv' salvato con successo!")

✅ File 'sasa_residues.csv' salvato con successo!
